In [1]:
from sklearn.datasets import make_regression, load_diabetes
from lightgbm import LGBMRegressor
import pandas as pd
import numpy as np
import re

## LightGBM

In [2]:
# Fitting a model
X, y = make_regression()
#df = load_diabetes(as_frame=True)
#X, y = df['data'], df['target']
lgb_reg = LGBMRegressor().fit(X, y)

In [3]:
feature_names = lgb_reg.booster_.feature_name()

In [4]:
if feature_names[0] == 'Column_0':
    print(trees_df['split_feature'].str[7:].apply(lambda x: int(x) if x is not None else x))

NameError: name 'trees_df' is not defined

In [50]:
trees_df = lgb_reg.booster_.trees_to_dataframe()
trees_df

tree_index  node_depth node_index left_child right_child parent_index  \
0             0           1       0-S0       0-S1        0-L1         None   
1             0           2       0-S1       0-L0        0-L2         0-S0   
2             0           3       0-L0       None        None         0-S1   
3             0           3       0-L2       None        None         0-S1   
4             0           2       0-L1       None        None         0-S0   
..          ...         ...        ...        ...         ...          ...   
695          99           2      99-S1      99-S2       99-L2        99-S0   
696          99           3      99-S2      99-L1       99-L3        99-S1   
697          99           4      99-L1       None        None        99-S2   
698          99           4      99-L3       None        None        99-S2   
699          99           3      99-L2       None        None        99-S1   

    split_feature     split_gain  threshold decision_type missing_direction  \
0       Column_91  662865.000000   0.444657            <=              left   
1       Column_12  406513.000000  -0.300151            <=              left   
2            None            NaN        NaN          None              None   
3            None            NaN        NaN          None              None   
4            None            NaN        NaN          None              None   
..            ...            ...        ...           ...               ...   
695     Column_90    1761.579956   0.241616            <=              left   
696     Column_90    1222.109985  -0.645137            <=              left   
697          None            NaN        NaN          None              None   
698          None            NaN        NaN          None              None   
699          None            NaN        NaN          None              None   

    missing_type      value  weight  count  
0           None -27.259200       0    100  
1           None -32.462500      71     71  
2           None -40.582262      33     33  
3           None -25.411137      38     38  
4           None -14.519948      29     29  
..           ...        ...     ...    ...  
695         None   0.207988      79     79  
696         None  -0.141902      51     51  
697         None   0.377311      24     24  
698         None  -0.603425      27     27  
699         None   0.845287      28     28  

[700 rows x 15 columns]

In [16]:
trees_df['missing'] = np.where(
    trees_df['missing_direction'] == 'left',
    trees_df['left_child'],
    trees_df['right_child']
)
trees_df = trees_df.drop(columns=['missing_direction'])

In [63]:
trees_df.head(10)

tree_index  node_depth node_index left_child right_child parent_index  \
0           0           1       0-S0       0-S1        0-L1         None   
1           0           2       0-S1       0-L0        0-L2         0-S0   
2           0           3       0-L0       None        None         0-S1   
3           0           3       0-L2       None        None         0-S1   
4           0           2       0-L1       None        None         0-S0   
5           1           1       1-S0       1-L0        1-S1         None   
6           1           2       1-L0       None        None         1-S0   
7           1           2       1-S1       1-L1        1-S2         1-S0   
8           1           3       1-L1       None        None         1-S1   
9           1           3       1-S2       1-L2        1-L3         1-S1   

  split_feature     split_gain  threshold decision_type missing_direction  \
0     Column_91  662865.000000   0.444657            <=              left   
1     Column_12  406513.000000  -0.300151            <=              left   
2          None            NaN        NaN          None              None   
3          None            NaN        NaN          None              None   
4          None            NaN        NaN          None              None   
5     Column_12  554203.000000  -0.774833            <=              left   
6          None            NaN        NaN          None              None   
7     Column_91  400332.000000  -0.419771            <=              left   
8          None            NaN        NaN          None              None   
9     Column_91   89868.703125   0.627751            <=              left   

  missing_type      value  weight  count  
0         None -27.259200       0    100  
1         None -32.462500      71     71  
2         None -40.582262      33     33  
3         None -25.411137      38     38  
4         None -14.519948      29     29  
5         None   0.000000       0    100  
6         None -13.247555      24     24  
7         None   4.183440      76     76  
8         None  -4.101336      33     33  
9         None  10.541500      43     43

## XGBoost

In [7]:
from xgboost import XGBRegressor

# Fitting a model
X, y = make_regression()
#X, y = df['data'], df['target']
xgb_reg = XGBRegressor().fit(X, y)

In [46]:
xgb_trees = xgb_reg.get_booster().trees_to_dataframe()
xgb_trees

Tree  Node    ID Feature     Split  Yes    No Missing          Gain  \
0        0     0   0-0     f83  0.564303  0-1   0-2     0-1  8.529987e+05   
1        0     1   0-1      f4 -0.796301  0-3   0-4     0-3  3.653044e+05   
2        0     2   0-2     f45 -0.623022  0-5   0-6     0-5  2.022018e+05   
3        0     3   0-3     f29 -0.253237  0-7   0-8     0-7  1.154759e+05   
4        0     4   0-4     f19  0.565895  0-9  0-10     0-9  2.547567e+05   
...    ...   ...   ...     ...       ...  ...   ...     ...           ...   
2253    95     0  95-0    Leaf       NaN  NaN   NaN     NaN -4.744766e-08   
2254    96     0  96-0    Leaf       NaN  NaN   NaN     NaN -4.744766e-08   
2255    97     0  97-0    Leaf       NaN  NaN   NaN     NaN -4.744766e-08   
2256    98     0  98-0    Leaf       NaN  NaN   NaN     NaN -4.744766e-08   
2257    99     0  99-0    Leaf       NaN  NaN   NaN     NaN -4.744766e-08   

      Cover  Category  
0     100.0       NaN  
1      69.0       NaN  
2      31.0       NaN  
3      18.0       NaN  
4      51.0       NaN  
...     ...       ...  
2253  100.0       NaN  
2254  100.0       NaN  
2255  100.0       NaN  
2256  100.0       NaN  
2257  100.0       NaN  

[2258 rows x 11 columns]

In [47]:
booster = xgb_reg.get_booster()
booster.feature_names

In [14]:
len(trees)

100

In [ ]:
# https://github.com/eli5-org/eli5/blob/69637074ad07cdb0d0aa3a650302a721c9272e4b/eli5/xgboost.py#L239
# https://stackoverflow.com/questions/62844000/is-there-any-way-to-calculate-the-values-at-each-node-in-xgboost-trees

In [54]:
# Regexes
feature_regex = re.compile('.*\:\[f(\d+).*')
threshold_regex = re.compile('.*\:\[f\d+<(\d+\.*\d+)]')
left_regex = re.compile('.*\:\[f\d+<\d+\.*\d+]\syes=(\d+)')
right_regex = re.compile('.*\:\[f\d+<\d+\.*\d+]\syes=\d+,no=(\d+)')

nodes_df = []

for tree_index, tree in enumerate(trees):    
    nodes = [st.strip() for st in trees[0].split('\n\t')]
    for node in nodes:
        
        node_index = node.split(':')[0]
        
        feature = int(feature_regex.search(node).group(1))
        threshold = float(threshold_regex.search(node).group(1))
        left_child = int(left_regex.search(node).group(1))
        right_child = int(right_regex.search(node).group(1))
        
        node_df = {
                'tree_index'        : tree_index,
                'node_depth'        : None,
                'node_index'        : node_index,
                'left_child'        : left_child,
                'right_child'       : right_child,
                'parent_index'      : None,
                'split_feature'     : feature,
                'split_gain'        : None,
                'threshold'         : threshold,
                'decision_type'     : None,
                'missing_direction' : None,
                'missing_type'      : None,
                'value'             : None,
                'weight'            : None,
                'count'             : None
        }
        nodes_df.append(node_df)
nodes_df = pd.DataFrame.from_records(nodes_df)

AttributeError: 'NoneType' object has no attribute 'group'

In [53]:
nodes_df

tree_index node_depth node_index  ...  value  weight count
0              0       None          0  ...   None    None  None
1              0       None          1  ...   None    None  None
2              0       None          3  ...   None    None  None
3              0       None          7  ...   None    None  None
4              0       None         15  ...   None    None  None
...          ...        ...        ...  ...    ...     ...   ...
5295          99       None         28  ...   None    None  None
5296          99       None         39  ...   None    None  None
5297          99       None         51  ...   None    None  None
5298          99       None         52  ...   None    None  None
5299          99       None         40  ...   None    None  None

[5300 rows x 15 columns]

In [39]:
st = '0:[f17<0.216996461] yes=1,no=2,missing=1'

# Feature
feature = re.compile('.*\:\[f(\d+).*')
feature.search(st).group(1)

# Threshold
threshold = re.compile('.*\:\[f\d+<(\d+\.*\d+)]')
threshold.search(st).group(1)

# Left 
left_regex = re.compile('.*\:\[f\d+<\d+\.*\d+]\syes=(\d+)')
left_regex.search(st).group(1)

# Right 
right_regex = re.compile('.*\:\[f\d+<\d+\.*\d+]\syes=\d+,no=(\d+)')
right_regex.search(st).group(1)

'2'

In [ ]:
nodes = []
for tree_index, tree in enumerate(sk_trees):
    tree = tree[0].tree_
    decision_type = '<='
    has_children = (tree.children_left != -1) & (tree.children_right != -1)


    df = pd.DataFrame({
        'tree_index'        : [tree_index] * tree.node_count,
        'node_depth'        : sklearn_compute_node_depths(tree),
        'node_index'        : list(range(0, tree.node_count)),
        'left_child'        : tree.children_left,
        'right_child'       : tree.children_right,
        'parent_index'      : sklearn_get_parent_idx(tree),
        'split_feature'     : tree.feature,
        'split_gain'        : None,
        'threshold'         : tree.threshold,
        'decision_type'     : [decision_type if hc else None for hc in has_children ],
        'missing_direction' : None,
        'missing_type'      : None,
        'value'             : tree.value.ravel(),
        'weight'            : None,
        'count'             : tree.n_node_samples 
    })
    nodes.append(df)

## CatBoost

In [8]:
from sklearn.datasets import make_regression, load_diabetes
from catboost import CatBoostRegressor

# Fitting a model
X, y = make_regression()
cb_reg = CatBoostRegressor().fit(X, y, verbose=False)

# Extracting trees

<frozen importlib._bootstrap>:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 216 from C header, got 232 from PyObject


In [7]:
obj = cb_reg._object

b'CBM1\xc0\xc1\x10\x00\x10\x00\x00\x00\x00\x00\n\x00\x10\x00\x04\x00\x08\x00\x0c\x00\n\x00\x00\x00$\x00\x00\x00\xfc\x16\x00\x00\x04\x00\x00\x00\x05\x00\x00\x00\x8c\x14\x00\x00\xa4\x10\x00\x00\xe4\x10\x00\x00 \x00\x00\x004\x14\x00\x00\x12\x00\x00\x00FlabuffersModel_v1\x00\x00\xa8\xeb\xff\xffl\x10\x00\x00\x04\x00\x00\x00_\x10\x00\x00{"detailed_profile":false,"boosting_options":{"model_shrink_mode":"Constant","approx_on_full_history":false,"fold_len_multiplier":2,"fold_permutation_block":0,"posterior_sampling":false,"boosting_type":"Plain","iterations":1000,"model_shrink_rate":0,"od_config":{"wait_iterations":20,"type":"None","stop_pvalue":0},"boost_from_average":true,"permutation_count":4,"learning_rate":0.028456000611186028},"pool_metainfo_options":{"tags":{}},"metrics":{"objective_metric":{"type":"RMSE","params":{}},"eval_metric":{"type":"RMSE","params":{}},"custom_metrics":[]},"metadata":{},"cat_feature_params":{"store_all_simple_ctr":false,"ctr_leaf_count_limit":18446744073709551615,

In [12]:
import json
import os

model_name = '_tmp.dump'
cb_reg.save_model('_tmp.dump', 'json')

with open(model_name) as f:
    trees_json = json.load(f)

os.remove(model_name)

In [20]:
trees_json.keys()

dict_keys(['features_info', 'model_info', 'oblivious_trees', 'scale_and_bias'])

In [21]:
oblivious_trees = trees_json['oblivious_trees']
features_info   = trees_json['features_info']

In [23]:
tree = oblivious_trees[0]

In [38]:
np.arange(2, 20, 2)

array([ 2,  4,  6,  8, 10, 12, 14, 16, 18])

In [44]:
df = []

for tree_index, tree in enumerate(oblivious_trees):
    tree_depth = len(tree['splits'])
    last_max = 0
    for node_depth, split in enumerate(tree['splits']):
        level_width = 2 ** node_depth
        next_level_width = 2 ** (node_depth + 1)
        current_max = last_max + level_width
        
        if node_depth == tree_depth:
            left_child = [None] * level_width
            right_child = [None] * level_width
            weight = tree['leaf_weights']
            value = tree['leaf_values']
        else:
            left_child = np.arange(current_max, current_max + next_level_width, 2)
            right_child = np.arange(current_max + 1, current_max + 1 + next_level_width, 2)
            weight = [None] * level_width
            value = [None] * level_width
        
        node_index = np.arange(last_max, last_max + level_width)
        node_index = [f'{tree_index}-{node_idx}' for node_idx in node_index]
        
        level_nodes = pd.DataFrame({
            'tree_index'        : [tree_index] * level_width,
            'node_depth'        : [tree_index] * level_width,
            'node_index'        : node_index,
            'left_child'        : left_child,
            'right_child'       : right_child,
            #'parent_index'      : None,
            #'split_gain'        : None,
            'split_feature'     : [split['float_feature_index']] * level_width,
            'threshold'         : [split['border']] * level_width,
            #'missing_direction' : None,
            #'missing_type'      : None,
            'value'             : value,
            'weight'            : weight,
            #'count'             : None 
        })  
        df.append(level_nodes)
        last_max += level_width
trees_df = pd.concat(df)          

In [45]:
trees_df

tree_index  node_depth node_index  left_child  right_child  split_feature  \
0            0           0        0-0           1            2             39   
0            0           0        0-1           3            4             39   
1            0           0        0-2           5            6             39   
0            0           0        0-3           7            8             81   
1            0           0        0-4           9           10             81   
..         ...         ...        ...         ...          ...            ...   
27         999         999     999-58         117          118             77   
28         999         999     999-59         119          120             77   
29         999         999     999-60         121          122             77   
30         999         999     999-61         123          124             77   
31         999         999     999-62         125          126             77   

    threshold value weight  
0    0.508094  None   None  
0   -0.380747  None   None  
1   -0.380747  None   None  
0    0.811609  None   None  
1    0.811609  None   None  
..        ...   ...    ...  
27   1.032720  None   None  
28   1.032720  None   None  
29   1.032720  None   None  
30   1.032720  None   None  
31   1.032720  None   None  

[63000 rows x 9 columns]

In [30]:
sum(tree['leaf_weights'])

100

In [5]:
# Internal object, which stores the trees
obj = cb_reg._object

# CatBoost general tree stats
obj._get_tree_count()
obj._get_tree_leaf_counts()

# Leaf values for tree 0
obj._get_tree_leaf_values(0)

# Get level splits 
obj._get_tree_node_to_leaf(0, None)

# 
obj._get_tree_splits(0, None)
#obj._get_tree_step_nodes(0)

TypeError: _get_tree_node_to_leaf() takes exactly one argument (2 given)

In [ ]:
#help(obj._get_tree_node_to_leaf)
obj._get_tree_node_to_leaf(1)

In [7]:
obj._get_tree_leaf_values()

TypeError: _get_tree_leaf_values() takes exactly one argument (0 given)

## scikit-learn

In [11]:
from sklearn.ensemble import GradientBoostingRegressor
gbm_reg = GradientBoostingRegressor().fit(X, y)
gbm_reg.estimators_

array([[DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
                              random_state=RandomState(MT19937) at 0x7F18B85B7E40)],
       [DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
                              random_state=RandomState(MT19937) at 0x7F18B85B7E40)],
       [DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
                              random_state=RandomState(MT19937) at 0x7F18B85B7E40)],
       [DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
                              random_state=RandomState(MT19937) at 0x7F18B85B7E40)],
       [DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
                              random_state=RandomState(MT19937) at 0x7F18B85B7E40)],
       [DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
                              random_state=RandomState(MT19937) at 0x7F18B85B7E40)],
       [DecisionTreeRegressor(criterion='friedman_mse', max_depth=3,
       

## skgbm

In [1]:
from skgbm.tools import trees_to_dataframe
from sklearn.datasets import make_regression

from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import GradientBoostingRegressor

In [2]:
# Creating data
X, y = make_regression()

# Regressors
xgb_reg = XGBRegressor().fit(X, y)
lgb_reg = LGBMRegressor().fit(X, y)
cb_reg = CatBoostRegressor().fit(X, y, verbose=False)
gb_reg = GradientBoostingRegressor().fit(X, y)

In [3]:
# Getting trees as dataframe
xgb_df = trees_to_dataframe(xgb_reg)
lgb_df = trees_to_dataframe(lgb_reg)
cb_df = trees_to_dataframe(cb_reg)
gb_df = trees_to_dataframe(gb_reg)

In [4]:
cb_df.columns

Index(['tree_index', 'node_depth', 'node_index', 'left_child', 'right_child',
       'split_feature', 'threshold', 'value', 'weight'],
      dtype='object')

In [4]:
lgb_df.columns

Index(['tree_index', 'node_depth', 'node_index', 'left_child', 'right_child',
       'parent_index', 'split_feature', 'split_gain', 'threshold',
       'decision_type', 'missing', 'missing_type', 'value', 'weight', 'count'],
      dtype='object')

In [10]:
xgb_reg

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             n_estimators=100, n_jobs=None, num_parallel_tree=None,
             predictor=None, random_state=None, ...)

In [5]:
gb_df

tree_index  node_depth  left_child  right_child  split_feature  threshold  \
0            0           1           1            8             23  -0.019940   
1            0           2           2            5             49   0.258042   
2            0           3           3            4             81  -0.769405   
3            0           4          -1           -1             -2  -2.000000   
4            0           4          -1           -1             -2  -2.000000   
..         ...         ...         ...          ...            ...        ...   
10          99           4          -1           -1             -2  -2.000000   
11          99           4          -1           -1             -2  -2.000000   
12          99           3          13           14             62   0.932407   
13          99           4          -1           -1             -2  -2.000000   
14          99           4          -1           -1             -2  -2.000000   

   decision_type         value  count  
0             <= -1.278977e-14    100  
1             <= -9.833694e+01     53  
2             <= -1.626777e+02     34  
3           None -3.904520e+02      5  
4           None -1.234063e+02     29  
..           ...           ...    ...  
10          None  1.009597e+00      1  
11          None  1.985299e+00      3  
12            <=  3.712195e-01     11  
13          None  6.318625e-01      9  
14          None -8.016739e-01      2  

[1484 rows x 9 columns]

In [14]:
xgb_reg.get_booster().trees_to_dataframe()

Tree  Node    ID Feature     Split  Yes    No Missing           Gain  \
0        0     0   0-0     f16 -0.742378  0-1   0-2     0-1  973352.188000   
1        0     1   0-1     f46  0.083533  0-3   0-4     0-3  216632.062000   
2        0     2   0-2     f57 -0.373606  0-5   0-6     0-5  769280.500000   
3        0     3   0-3      f4 -0.400372  0-7   0-8     0-7   49433.019500   
4        0     4   0-4     f98  0.826694  0-9  0-10     0-9  115805.750000   
...    ...   ...   ...     ...       ...  ...   ...     ...            ...   
2391    95     0  95-0    Leaf       NaN  NaN   NaN     NaN      -0.000002   
2392    96     0  96-0    Leaf       NaN  NaN   NaN     NaN      -0.000002   
2393    97     0  97-0    Leaf       NaN  NaN   NaN     NaN      -0.000002   
2394    98     0  98-0    Leaf       NaN  NaN   NaN     NaN      -0.000001   
2395    99     0  99-0    Leaf       NaN  NaN   NaN     NaN      -0.000001   

      Cover  Category  
0     100.0       NaN  
1      22.0       NaN  
2      78.0       NaN  
3       8.0       NaN  
4      14.0       NaN  
...     ...       ...  
2391  100.0       NaN  
2392  100.0       NaN  
2393  100.0       NaN  
2394  100.0       NaN  
2395  100.0       NaN  

[2396 rows x 11 columns]

In [8]:
cb_reg.plot_tree(
    tree_idx=0
).render(filename='img/g1.png')

'img/g1.pdf'